<a href="https://colab.research.google.com/github/patrickvonplaten/notebooks/blob/master/BERT2BERT_for_CNN_Dailymail.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## **Warm-starting bart for CNN/Dailymail**

***Note***: This notebook only uses a few training, validation, and test data samples for demonstration purposes. To fine-tune an encoder-decoder model on the full training data, the user should change the training and data preprocessing parameters accordingly as highlighted by the comments.


### **Data Preprocessing**


In [1]:
%%capture
!pip install datasets
!pip install transformers
!pip install starcc
!pip install evaluate

In [2]:
import json
from StarCC import PresetConversion
convert = PresetConversion(src='cn', dst='hk', with_phrase=False)

with open("train/botisan.json", "r") as botisan_file, open("train/tatoeba.tsv", "r") as tatoeba_file, open("train/train.can", "w+") as can_file, open("train/train.man", "w+") as man_file:
    for line in botisan_file.readlines():
        translation = json.loads(line)["translation"]
        can_file.write(translation["yue"] + "\n")
        man_file.write(convert(translation["zh"]) + "\n")
    
    for line in tatoeba_file.read().splitlines():
        [_, can, _, man] = line.split("\t")
        can_file.write(can + "\n")
        man_file.write(convert(man) + "\n")


Building prefix dict from the default dictionary ...
Loading model from cache /var/folders/kk/n4ff6h1n3t170b1m4zv09yf40000gn/T/jieba.cache
Loading model cost 0.336 seconds.
Prefix dict has been built successfully.


In [3]:
from os import listdir
from os.path import isfile, join
man_dir = "train/man/"
can_dir = "train/can/"
man_paths = [f for f in listdir(man_dir) if isfile(join(man_dir, f)) and f != ".DS_Store"]
with open("train/train.can", "a+") as can_train_file, open("train/train.man", "a+") as man_train_file:
    for man_path in man_paths:
        with open(man_dir + man_path, "r") as man_file:
            name = man_path[len("man-"):len("man-")+2]
            can_path = "can-" + name + ".txt"
            with open(can_dir + can_path, "r") as can_file:
                for man_line, can_line in zip(man_file.readlines(), can_file.readlines()):
                    can_train_file.write(can_line)
                    man_train_file.write(man_line)

In [20]:
from datasets import Dataset

train_data = None
val_data = None
test_data = None

with open("train/train.can", "r") as can_file, open("train/train.man", "r") as man_file:
    train_data = Dataset.from_dict({"can": can_file.read().splitlines(), "man": man_file.read().splitlines()})
    print(f"Loaded training data.")
    print(f"First line: {train_data[0]}")

with open("para/dev/dev.can", "r") as can_file, open("para/dev/dev.man", "r") as man_file:
    val_data = Dataset.from_dict({"can": can_file.read().splitlines(), "man": man_file.read().splitlines()})
    print(f"Loaded validation data.")
    print(f"First line: {val_data[0]}")

with open("para/test/test.can", "r") as can_file, open("para/test/test.man", "r") as man_file:
    test_data = Dataset.from_dict({"can": can_file.read().splitlines(), "man": man_file.read().splitlines()})
    print(f"Loaded test data.")
    print(f"First line: {test_data[0]}")


Loaded training data.
First line: {'can': '杞人嘅朋友嘆咗一口氣', 'man': '杞人的朋友嘆了一口氣'}
Loaded validation data.
First line: {'can': '啲咁耐就攪掂嘞，真係掯', 'man': '他一會兒工夫就弄好了，真神'}
Loaded test data.
First line: {'can': '筷子放喺你嘅右便', 'man': '筷子放在你的右邊'}


In [5]:
from transformers import BertTokenizer

tokenizer = BertTokenizer.from_pretrained('Ayaka/bart-base-cantonese')
tokenizer.bos_token = tokenizer.cls_token
tokenizer.eos_token = tokenizer.sep_token

In [6]:
batch_size=32  # change to 16 for full training
encoder_max_length=100
decoder_max_length=100

def process_data_to_model_inputs(batch):
  # tokenize the inputs and labels
  inputs = tokenizer(batch["can"], padding="max_length", truncation=True, max_length=encoder_max_length)
  outputs = tokenizer(batch["man"], padding="max_length", truncation=True, max_length=decoder_max_length)

  batch["input_ids"] = inputs.input_ids
#   batch["attention_mask"] = inputs.attention_mask
#   batch["decoder_input_ids"] = outputs.input_ids
#   batch["decoder_attention_mask"] = outputs.attention_mask
  batch["labels"] = outputs.input_ids.copy()

  # because BERT automatically shifts the labels, the labels correspond exactly to `decoder_input_ids`. 
  # We have to make sure that the PAD token is ignored
  batch["labels"] = [[-100 if token == tokenizer.pad_token_id else token for token in labels] for labels in batch["labels"]]

  return batch

# only use 32 training examples for notebook - DELETE LINE FOR FULL TRAINING
# train_data = train_data.select(range(32))

train_data = train_data.map(
    process_data_to_model_inputs, 
    batched=True, 
    batch_size=batch_size,
)
train_data.set_format(
    # type="torch", columns=["input_ids", "attention_mask", "decoder_input_ids", "decoder_attention_mask", "labels"],
    type="torch", columns=["input_ids", "labels"],
)


# only use 16 training examples for notebook - DELETE LINE FOR FULL TRAINING
# val_data = val_data.select(range(16))

val_data = val_data.map(
    process_data_to_model_inputs, 
    batched=True, 
    batch_size=batch_size,
)
val_data.set_format(
    # type="torch", columns=["input_ids", "attention_mask", "decoder_input_ids", "decoder_attention_mask", "labels"],
    type="torch", columns=["input_ids", "labels"],
)

Map:   0%|          | 0/80283 [00:00<?, ? examples/s]

Map:   0%|          | 0/6502 [00:00<?, ? examples/s]

### **Warm-starting the Encoder-Decoder Model**

In [7]:
# from transformers import EncoderDecoderModel
from transformers import BartForConditionalGeneration

bart = BartForConditionalGeneration.from_pretrained('Ayaka/bart-base-cantonese')
# bart = EncoderDecoderModel.from_encoder_decoder_pretrained("Ayaka/bart-base-cantonese", "Ayaka/bart-base-cantonese")

In [8]:
# set special tokens
bart.config.decoder_start_token_id = tokenizer.bos_token_id
bart.config.eos_token_id = tokenizer.eos_token_id
bart.config.pad_token_id = tokenizer.pad_token_id

# sensible parameters for beam search
# bart.config.vocab_size = bart.config.decoder.vocab_size
bart.config.max_length = 100
bart.config.min_length = 3
# bart.config.no_repeat_ngram_size = 3
bart.config.early_stopping = True
# bart.config.length_penalty = 2.0
bart.config.num_beams = 4

### **Fine-Tuning Warm-Started Encoder-Decoder Models**

In [58]:
import sacrebleu

def compute_metrics(pred):
    # print("Start compute_metrics")
    labels_ids = pred.label_ids
    pred_ids = pred.predictions

    # all unnecessary tokens are removed
    pred_str = [s.replace(" ", "") for s in tokenizer.batch_decode(pred_ids, skip_special_tokens=True)]
    print("Predicted:", pred_str)
    labels_ids[labels_ids == -100] = tokenizer.pad_token_id
    label_str = [s.replace(" ", "") for s in tokenizer.batch_decode(labels_ids, skip_special_tokens=True)]
    print("Target:", label_str)

    # bleu_score = bleu.compute(predictions=pred_str, references=label_str, tokenizer=char_tokenizer)["bleu"]
    # chrf_score = chrf.compute(predictions=pred_str, references=label_str)["score"]

    bleu = sacrebleu.BLEU(trg_lang="zh")
    bleu_score = bleu.corpus_score(pred_str, [label_str]).score

    chrf = sacrebleu.CHRF()
    chrf_score = chrf.corpus_score(pred_str, [label_str]).score

    return {
        "bleu": bleu_score,
        "chrf": chrf_score,
    }

In [57]:
# Test CharBLEU
predictions = ['我啲咁耐就攪掂嘞，真係掯', '你幾時得嚟吖']
references = ['我啲咁耐就攪掂嘞，真係掯', '你幾時得嚟吖']

bleu = sacrebleu.BLEU(trg_lang="zh")
bleu_score = bleu.corpus_score(predictions, [references]).score
assert bleu_score - 100 <= 1e-9

Cool! Finally, we start training.

In [16]:
from transformers import Seq2SeqTrainer, Seq2SeqTrainingArguments

import warnings
warnings.filterwarnings('ignore')

# set training arguments - these params are not really tuned, feel free to change
training_args = Seq2SeqTrainingArguments(
    output_dir="./",
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    predict_with_generate=True,
    use_mps_device=True,
    do_train=True,
    evaluation_strategy="steps",
    do_eval=True,
    logging_steps=200,  # set to 1000 for full training
    save_steps=1000,  # set to 500 for full training
    eval_steps=1000,  # set to 8000 for full training
    warmup_steps=1000,  # set to 2000 for full training
    # max_steps=10, # delete for full training
    overwrite_output_dir=True,
    save_total_limit=5,
    fp16=False,
)

# instantiate trainer
trainer = Seq2SeqTrainer(
    model=bart,
    args=training_args,
    compute_metrics=compute_metrics,
    train_dataset=train_data,
    eval_dataset=val_data.select(range(batch_size * 50)),
)
trainer.train()

  0%|          | 0/7527 [00:00<?, ?it/s]

{'loss': 0.0687, 'learning_rate': 1e-05, 'epoch': 0.08}
{'loss': 0.0565, 'learning_rate': 2e-05, 'epoch': 0.16}
{'loss': 0.0463, 'learning_rate': 3e-05, 'epoch': 0.24}
{'loss': 0.0388, 'learning_rate': 4e-05, 'epoch': 0.32}
{'loss': 0.0276, 'learning_rate': 5e-05, 'epoch': 0.4}


  0%|          | 0/50 [00:00<?, ?it/s]

Predicted: ['這些那久就攪定了，真的掯', '幾時得嚟吖', '佢望了他爸爸一眼', '他鬼咁神經失常，講話好似雞啄不斷噉', '佢騙了我好多錢', '將這些錢給他', '我畀了三次錢你', '戴了頂紅色的帽', '的有幾重', '到死！', '有幾何吖，沒有什麼幾何而已', '呢度得佢一個人咋', '佢好俊男', '同你講過嘅喇，是不是先', '廣東話讀歪一些就是普通話了', '有什麼順東西吖？', '看過三次戲', '你借錢我', '佢畀三本書我', '他逼我叫你選他做班長', '送枝筆他', '你估你好叻呀！', '佢嗌亞黃去', '佢夾硬搶咗我三粒糖', '做完啲功課', '我啲錢', '將張桌子擦一擦', '我借五蚊你，你連句感謝都無', '將這些衫洗了', '人哋寫字你不要在此喐喐貢', '寫封信給媽媽', '與敵人拼命', '拎杯茶給我', '嗰間店鋪賺了我五蚊', '你借我錢', '我借你五蚊，遲早還是要還給你㗎', '這個老闆仍欠伙記三個月人工', '你就勸他不要哭喇！', '你別逼我做這樣的事！', '你這樣的話做法，正一攞苦至辛！', '拎嗰啲嘢出至', '我當他好人添！', '我請你食飯', '我對筷子', '我教了你十年英文', '生得真的醜怪', '生得真的醜樣', '真冇解八點鐘仲未有人至', '條命凍過水', '無謂攪咁多嘢喇', '生得像你', '我麻煩你一件事', '下午開會嗎？', '乜鬼嘢都唔想要', '教咗幾十年書', '洗咗啲衫', '畀他打了一下', '送枝筆給他', '我教了這一科十年', '我本書', '我問你一個問題', '亞郭叫我幫他太太查師傅教車', '一邊唞涼一邊傾引伸為話語', '這個嬰孩仔好可愛', '你去唔去呀？', '這套戲看得吖', '你要不要啊？', '你話幾般美呢', '你看他個樣幾得敕', '這個地方冇乜好玩', '你叫什麼名呀？', '你們在這裏搗亂，別人都沒辦法休息喇', '你唔去呀？', '他站在出便', '你躝了去哪裏？', '他這個人鬼五馬六的事零舍多', '佢好打得', '他沒錯吖，為什麼説他呢？', '他的作風那鬼馬，好人都有限嘞', '你認為怎麼辦呢？', '佢想搵你講', '你都大仔喇', '他購物很醃尖的', '你以為那著數咩', '佢生得好俊男', '他不算醃

  0%|          | 0/50 [00:00<?, ?it/s]

...

  0%|          | 0/50 [00:00<?, ?it/s]

Predicted: ['這些那久就完成了，真掯', '什麼時候得來吖', '他望了他爸爸一眼', '他鬼死氣，講話好像雞啄不斷地', '他騙了我好多錢', '將這些錢給他', '我給了三次錢你', '戴了頂紅色的帽', '的有幾重', '到死！', '有幾何吖，沒怎麼幾何而已', '這個地方得他一個人咋', '他很俊男', '跟你講過的了，是不是先', '廣東話讀歪一些就是普通話了', '有什麼順東西嗎？', '看過三次戲', '你借錢我', '他給予三本書我', '他逼我叫你選他做班長', '送枝筆他', '你估你很聰明嗎！', '他喊亞黃去', '他強行搶了我三粒糖', '做完這些功課', '我這些錢', '把張桌子擦一擦', '我借五蚊你，你連句感謝都無', '把這些衣服洗了', '人家寫字你不要在這裏喐喐貢', '寫封信給媽媽', '與敵人拼命', '持杯茶給我', '那間店鋪賺了我五蚊', '你借我錢', '我借你五蚊，遲早還是要還給你的', '這個老闆仍欠員工三個月工資', '你就勸一下他不要哭喇！', '你別逼我做這樣的事！', '你這樣的話做法，正一拿苦至辛！', '持嗰些東西出至', '我當他好人添！', '我請你吃飯', '我對筷子', '我教了你十年英文', '長得十分醜怪', '長得真的醜樣', '真沒解八點鐘仍未有人至', '條命凍過水', '無謂攪這麼多事情喇', '長得像你', '我麻煩你一件事', '下午開會嗎？', '什麼鬼東西都不想要', '教了幾十年書', '洗了這些衫', '給他打了一下', '送枝筆給他', '我教了這一科十年', '我本書', '我問你一個問題', '亞郭叫我幫他太太查師傅教車', '一邊唞涼一邊聊天', '這個嬰孩仔好可愛', '你去不去呀？', '這套電影看得啊', '你要不要啊？', '你說多麼漂亮呢', '你看他的樣子幾得敕', '這個地方沒有什麼好玩', '你叫什麼名字？', '你們在搗亂，別人都沒辦法休息了', '你不去嗎？', '他站在外邊', '你爬了去哪裏？', '他這個人鬼五馬六的事零舍多', '他很打得', '他沒錯啊，為什麼説他呢？', '他的作風那鬼馬，好人都有限了', '你説怎麼辦呢？', '他想找你聊聊', '你都大仔喇', '他購物很醃尖的', '你以為那著數咩', '他長

  0%|          | 0/50 [00:00<?, ?it/s]

Predicted: ['這些那久就完成了，真掯', '什麼時候得來吖', '他望了他爸爸一眼', '他鬼般生氣，講話好像雞啄不斷地', '他騙了我好多錢', '將這些錢給他', '我給了三次錢你', '戴了頂紅色的帽', '的有幾重', '到死！', '有幾何吖，沒怎麼幾何而已', '這個地方得他一個人咋', '他很俊男', '跟你講過的了，是不是先', '廣東話讀歪一些就是普通話了', '有什麼順東西嗎？', '看過三次戲', '你借錢我', '他給予三本書我', '他逼我叫你選他做班長', '送枝筆他', '你估你很聰明嗎！', '他命令亞黃去', '他強行搶了我三粒糖', '做完這些功課', '我這些錢', '把張桌子擦一擦', '我借五蚊你，你連句感謝都無', '把這些衣服洗了', '人家寫字你不要在這裏喐喐貢', '寫封信給媽媽', '與敵人拼命', '持杯茶給我', '那間店鋪賺了我五蚊', '你借我錢', '我借你五蚊，遲早還是要還給你的', '這個老闆仍欠員工三個月工資', '你就勸一下他不要哭喇！', '你別逼我做這樣的事！', '你這樣的話做法，正一拿苦至辛！', '持嗰些東西出至', '我當他好人添！', '我請你吃飯', '我對筷子', '我教了你十年英文', '長得十分醜怪', '長得十分醜樣', '真沒解八點鐘仍未有人至', '條命凍過水', '無謂攪這麼多事情喇', '長得像你', '我麻煩你一件事', '下午開會嗎？', '什麼鬼東西都不想要', '教了幾十年書', '洗了些衫', '給他打了一下', '送枝筆給他', '我教了這一科十年', '我本書', '我問你一個問題', '亞郭叫我幫他太太查師傅教車', '一邊唞涼一邊聊天', '這個嬰孩仔好可愛', '你去不去呀？', '這套電影看得吖', '你要不要啊？', '你說多麼漂亮呢', '你看他的樣子幾得敕', '這個地方沒有什麼好玩', '你叫什麼名字呀？', '你們在搗亂，別人都沒辦法休息了', '你不去嗎？', '他站在外邊', '你爬了去哪裏？', '他這個人鬼五馬六的事零舍多', '他很打得', '他沒錯啊，為什麼説他呢？', '他的作風般鬼馬，好人都有限了', '你説怎麼辦呢？', '他想找你聊聊', '你都大仔喇', '他購物很醃尖的', '你以為那著數咩', '

TrainOutput(global_step=7527, training_loss=0.044586458924568334, metrics={'train_runtime': 8124.0289, 'train_samples_per_second': 29.646, 'train_steps_per_second': 0.927, 'train_loss': 0.044586458924568334, 'epoch': 3.0})

### **Evaluation**

Awesome, we finished training our dummy model. Let's now evaluated the model on the test data. We make use of the dataset's handy `.map()` function to generate a summary of each sample of the test data.

In [21]:
from transformers import BertTokenizer, BartForConditionalGeneration

tokenizer = BertTokenizer.from_pretrained('Ayaka/bart-base-cantonese')
model = BartForConditionalGeneration.from_pretrained("./checkpoint-7000").to('mps')

# only use 16 training examples for notebook - DELETE LINE FOR FULL TRAINING
# test_data = test_data.select(range(16))

batch_size = 64  # change to 64 for full evaluation

pred_file = open("test.pred.man", "w+")

# map data correctly
def generate_summary(batch):
    # Tokenizer will automatically set [BOS] <text> [EOS]
    # cut off at BERT max length 512
    inputs = tokenizer(batch["can"], padding="max_length", truncation=True, max_length=100, return_tensors="pt")
    input_ids = inputs.input_ids.to('mps')
    attention_mask = inputs.attention_mask.to('mps')

    outputs = model.generate(input_ids, attention_mask=attention_mask)

    # all special tokens including will be removed
    output_str = tokenizer.batch_decode(outputs, skip_special_tokens=True)
    batch["pred"] = [s.replace(" ", "") for s in output_str]
    for man, pred in zip(batch["man"], batch["pred"]):
        pred_file.write("P: " + pred + "\n")
        pred_file.write("T: " + man + "\n\n")
    return batch

results = test_data.map(generate_summary, batched=True, batch_size=batch_size)

pred_str = results["pred"]
label_str = results["man"]

bleu_score = bleu.compute(predictions=pred_str, references=label_str, tokenizer=char_tokenizer)["bleu"]
chrf_score = chrf.compute(predictions=pred_str, references=label_str)["score"]

print("BLEU score:", bleu_score)
print("CHRF score:", chrf_score)


Map:   0%|          | 0/6502 [00:00<?, ? examples/s]

BLEU score: 0.5128642563768376
CHRF score: 25.634135094120243


In [38]:
pred_str = results["pred"]
print(len("".join(pred_str)))
print(len(pred_str))
print(pred_str)

66858
6502
['筷子放在你的右便', '度處都見得到', '度處都是一樣', '度處都那乾淨', '這次他怎麼思索也沒符的了', '這件事，真的無符喇', '他百厭成這樣，他媽都沒完沒了', '他不交租你都無符', '都不夠麻將腳，點開桌子呀？', '不用找數喇', '今天這餐我找數', '他是左撓來的，用左手抓筷子', '他左撓，不做得這些事情', '琴夜晚食多了，今天肚膩', '肉煲不腍', '我些牙不要，要吃點膩東西', '你個人那膩，怎麼管得住班下屬？', '這些泥路，一下雨就膩嬰孩！', '這些豆腐腍啤啤很難夾', '這條路腍啤啤，車不行得', '豆腐般腍', '牛肉燜得很膩', '他這個人真膩，話都不多句', '他那腍善，人人都喜歡他', '我們的班主任很腍善', '白豆要漚長時間至腍', '把竹蔑掉落石灰池漚才', '這些穀來不及曬，有些漚了咯', '笑到他好像烚熟狗頭一樣', '一見到我就烚熟狗頭這樣，不謊有好東西啦', '這煮煮要烚兩個小時', '這次我撐硬你吖', '他一整天落酒吧飲酒', '他們兩個都是蒲精，總是加酒吧飲酒抽菸溝女', '那裏有個賣魚的攤檔', '這件事很順攤', '有人幫忙就順檔一些', '這次面試他穩定過抬油', '你不用急，他穩定過抬油', '事情那急他仍那定當', '我們拍硬檔辦好學校', '大家要拍硬檔才做得好工作的', '全靠大家攆硬檔，才能這樣子快攪得妥', '碗生漬', '單有好多漬洗不甩', '住他！', '班警察住，不出手', '死仔包，東西嗎？', '吃東西不要勢兇夾狼才行的', '看他勢兇夾狼，想食人這樣', '你想一就起十幢樓，真的是勢兇夾狼', '關你鬼事咩！', '牛筋般煙癮', '看他倆這麼煙蔫韌，就來結婚定了', '他們一早就為自己開啟了太平門，申請移民外國', '看清楚一些，打你的對與否嗰個人？', '我看白他會在會上發言的', '我看白他不來了', '看白他個病好不翻啦', '我看白他不會至', '一天看二三十個症', '醫生在這裏看症，沒空', '香港腳好多時候是很難斷尾的', '這的慢性病是很難斷尾的', '食了幾劑藥就斷尾咯', '這個玩具有出廠證明書，包無花假', '他講的都是實話，沒有什麼花假的', '這些東西好花假的', '他和老人家最多話講', '這個工程師好使得',

In [39]:
label_str = results["man"]
print(len("".join(label_str)))
print(len(label_str))
print(label_str)

69598
6502
['筷子放在你的右邊', '到處都看見', '處處都是一樣', '到處都那麼乾淨', '這次他怎麼想計謀也沒法解脫了', '這件事，真是沒辦法了', '他這麼淘氣，他媽媽也毫無辦法', '他不交租你也沒轍兒', '打麻將的伴兒還沒湊齊，怎麼開始啊？', '不必找錢了', '今天這頓飯，我來付款', '他是左撇子，用左手拿筷子', '他左撇捩，幹不了這些工作', '昨夜多吃了，今天肚子不舒服', '這肉煮不爛', '我的牙不好，要吃軟和的東西', '你這麼軟弱，怎能管得住那群部下？', '這些黃泥路，一下雨就是一片稀爛！', '這豆腐軟綿綿的不容易夾起來', '這條路軟綿綿的，車子走不了', '豆腐那樣軟', '牛肉燉得很爛', '他這個人真蔫，話也不多說一句', '他那麼和藹可親，人人都喜歡他', '我們班主任很溫和', '黃豆要熬很久才爛', '先把篾片扔進石灰池浸泡一下', '這些稻穀來不及曬乾，有一些霉爛了', '笑得他齜牙咧嘴', '他一見到我就笑得呲牙咧嘴的，一定沒什麼好事', '這鍋粽子要熬兩小時', '這次我一定支持你啊！', '他老去酒吧喝酒', '他們兩個都很貪玩，總是去酒吧喝酒抽煙泡妞', '那邊有一個賣魚的攤兒', '這件事很順利', '有人幫忙就順利一點', '這次面試他非常鎮定', '你不必著急，他心裡有數', '事情那麼緊急他還那麼穩', '我們為了辦好學校而緊密地合作', '我們要緊密地配合才能把工作做好', '全靠大家同心協力，才這麼快就搞好了', '碗積滿了垢', '床單有很多髒東西洗不掉', '盯死他！', '那幫警察正監視著，下不了手', '死東西，偷窺我的私處啊？', '吃東西不要狼吞虎嚥', '看他來勢洶洶的樣子，要把人吃掉似的', '你想一下子就建十幢樓房，真是胃口大', '關你屁事！', '像牛筋那麼韌', '瞧他倆這麼黏乎，快要結婚了吧', '他們早就給自己準備後路了，申請移民外國', '看清楚點兒，打你的是不是那個人？', '我斷定他會在會上發言的', '我早就斷定他不來的了', '看得出來他很難痊愈', '我可以斷定他不會來', '一天治二三十個病人', '醫生正在替病人治病，沒空', '腳氣很多時候是很難根治的', '這種慢性病是很難根治的', '吃了幾服藥就全好了', '這個玩具有產品說明

In [62]:
bleu = sacrebleu.BLEU(trg_lang="zh")
bleu_score = bleu.corpus_score(label_str, [pred_str]).score
print(bleu_score)

29.77679252318913
